In [220]:
import pandas as pd  # stress hydrique and rendement, besoin en eau
import plotly.graph_objects as go
from typing import List
import plotly.express as px

cols_to_keep = [
    "Precipitation (mm)",
    "Near Surface Air Temperature (°C)",
    "Surface Downwelling Shortwave Radiation (W/m²)",
    "year",
    "period",
]


def concatenate_historic_forecast(historic, forecast, cols_to_keep):
    historic["period"] = "historique"
    forecast["period"] = "forecast"
    historic = historic[cols_to_keep]
    forecast = forecast[cols_to_keep]
    full_data = pd.concat([historic, forecast])
    return full_data


def visualize_climate(
    moderate: pd.DataFrame,  # TODO: single dataframe
    historic: pd.DataFrame,
    x_axis="year",
    column: str = "Precipitation (mm)",
    cols_to_keep: List[str] = [
        "Precipitation (mm)",
        "Near Surface Air Temperature (°C)",
        "Surface Downwelling Shortwave Radiation (W/m²)",
        "year",
        "period",
    ],
):
    concatenated_df = concatenate_historic_forecast(moderate, historic, cols_to_keep)
    concatenated_df = concatenated_df.sort_values(by=x_axis)  # Ensure order

    fig = go.Figure()
    # colors = {"historique": "blue", "forecast": "purple"}

    for condition_value in concatenated_df["period"].unique():
        segment = concatenated_df[concatenated_df["period"] == condition_value]
        fig.add_trace(go.Scatter(x=segment[x_axis], y=segment[column], 
                             mode='lines', 
                             name=f'Condition {condition_value}', 
                             line=dict(color='blue' if condition_value == 'historique' else 'purple')))

    interpolation_df = concatenated_df[concatenated_df[x_axis]>2023]
    fig.add_trace(go.Scatter(x=interpolation_df[x_axis], 
                            y=interpolation_df[column].interpolate(), 
                            mode='lines', 
                            name='', 
                            line=dict(color='blue'),showlegend=False),
                            )

    fig.update_layout(
        title=f"Historique et Forecast pour {column}",
        xaxis_title="Date",
        yaxis_title=column,
    )

    return fig

In [221]:
cols_to_plot = [
    "Precipitation (mm)",
    "Near Surface Air Temperature (°C)",
    "Surface Downwelling Shortwave Radiation (W/m²)",
]
x_axes = ["year"]*len(cols_to_plot)


def aggregate_yearly(df, col_to_agg):
    df[col_to_agg] = df.groupby('year')[col_to_agg].transform('mean')
    return df

def generate_plots(
    moderate: pd.DataFrame,
    historic: pd.DataFrame,
    x_axes: List[str],
    cols_to_plot: List[str],
):
    plots = []
    for i,col in enumerate(cols_to_plot):
        plots.append(visualize_climate(moderate, historic, x_axes[i], col))
    return plots

In [222]:
from data_pipelines.historical_weather_data import (
    download_historical_weather_data,
    aggregate_hourly_weather_data,
)

latitude = 47
longitude = 5
start_year = 2000
end_year = 2025
df = download_historical_weather_data(latitude, longitude, start_year, end_year)
historic = aggregate_hourly_weather_data(df)
historic= historic.reset_index()
historic = historic.rename(
    columns={
        "precipitation": "Precipitation (mm)",
        "air_temperature_mean": "Near Surface Air Temperature (°C)",
        "irradiance": "Surface Downwelling Shortwave Radiation (W/m²)",
        'index': 'time'
    }
)
historic["time"] = pd.to_datetime(historic["time"])
historic = historic.sort_values('time')
historic = historic[historic["time"]<"2025-01-01"]


Coordinates 46.99472427368164°N 4.967532157897949°E
Elevation 201.0 m asl
Timezone None None
Timezone difference to GMT+0 0 s


In [223]:
root = "/Users/akramsanad/Documents/hackathon/"
moderate = pd.read_csv(f"{root}data/final_climate_data.csv")
moderate["time"] = pd.to_datetime(moderate["time"])
moderate = moderate.sort_values('time')
moderate['year'] = moderate["time"].dt.year
historic['year'] = historic["time"].dt.year
moderate["Precipitation (mm)"] = moderate["Precipitation (mm)"]*3600
for col in cols_to_plot:
    moderate = aggregate_yearly(moderate, col)
    historic = aggregate_yearly(historic, col)

In [224]:
plots = generate_plots(moderate, historic, x_axes, cols_to_plot)

In [225]:
for plot in plots:
    plot.show() 

### Second part

In [ ]:
cols = ["Evaporation (including sublimation and transpiration) (mm)"]